In this notebook we perform experiments about the capabilities of LLMs of understanding the legality of moves in board games. 

We focus on the board game Chef's Hat (https://whisperproject.eu/chefshat). The rulebook is available at (https://github.com/pablovin/ChefsHatGYM/blob/master/gitImages/RulebookMenuv08.pdf).

In particular, the players have agency only on the first two phases of each round, and most of the decisions take in place during the second phase, which is the focus of this project work.

In this phase, players can either or play a hand of cards; the played cards must be played on top the cards already present on the board, and all of the cards must have the same value, which must be lower than the value of cards on the board. Moreover, it is not possible to play less cards than the amount of cards that are already on the board. Jokers can replace any card when played on the board, and any card can be put on top of them.

# Importing and cleaning data

We begin by creating our dataframe:

In [1]:
import pickle
import pandas as pd
import numpy as np
import torch
import transformers
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig  

random_state = 1

with open('Dataset.pkl', 'rb') as f:
    data = pickle.load(f)

C:\Users\alfio\AppData\Local\Temp\ipykernel_19524\1749059438.py:12: DeprecationWarning: numpy.core.numeric is deprecated and has been renamed to numpy._core.numeric. The numpy._core namespace contains private NumPy internals and its use is discouraged, as NumPy internals can change without warning in any release. In practice, most real-world usage of numpy.core is to access functionality in the public NumPy API. If that is the case, use the public NumPy API. If not, you are using NumPy internals. If you would still like to access an internal attribute, use numpy._core.numeric._frombuffer.
  data = pickle.load(f)


We use the Hamming distance in order to measures (dis)similarity between instances.

In [2]:
def hamming(s1, s2):
    if len(s1) != len(s2):
        raise ValueError("Undefined for sequences of unequal length")
    return sum(ch1 != ch2 for ch1, ch2 in zip(s1, s2))   

In [3]:
def IoU_lists(s1: list[str], s2: list[str]) -> float:
    set1, set2 = set(s1), set(s2)
    return len(set1 & set2) / len(set1 | set2)

We inspect the attributes of the dataset; we will focus only on the "DISCARD" actions.

In [4]:
print(data.columns)
data

Index(['Match', 'Round', 'Agent_Names', 'Source', 'Action_Type',
       'Action_Description', 'Player_Finished', 'Player_Hands', 'Board_Before',
       'Board_After', 'Possible_Actions', 'Current_Roles', 'Match_Score',
       'Game_Score', 'Game_Performance_Score'],
      dtype='object')


Match  Round  \
2024-11-21_15:03:51.314611      0      0   
2024-11-21_15:03:51.314611      1      0   
2024-11-21_15:03:51.315609      1      0   
2024-11-21_15:03:51.327717      1      1   
2024-11-21_15:03:51.336602      1      1   
...                           ...    ...   
2024-11-21_15:06:08.055500    100     26   
2024-11-21_15:06:08.067496    100     26   
2024-11-21_15:06:08.070494    100     26   
2024-11-21_15:06:08.341109    100     26   
2024-11-21_15:06:08.345109    100     26   

                                                             Agent_Names  \
2024-11-21_15:03:51.314611  [RANDOM_01, RANDOM_02, RANDOM_03, RANDOM_04]   
2024-11-21_15:03:51.314611                                           NaN   
2024-11-21_15:03:51.315609                                           NaN   
2024-11-21_15:03:51.327717                                           NaN   
2024-11-21_15:03:51.336602                                           NaN   
...                                                                  ...   
2024-11-21_15:06:08.055500                                           NaN   
2024-11-21_15:06:08.067496                                           NaN   
2024-11-21_15:06:08.070494                                           NaN   
2024-11-21_15:06:08.341109                                           NaN   
2024-11-21_15:06:08.345109                                           NaN   

                               Source       Action_Type Action_Description  \
2024-11-21_15:03:51.314611     SYSTEM  START_EXPERIMENT                NaN   
2024-11-21_15:03:51.314611     SYSTEM         NEW_MATCH                NaN   
2024-11-21_15:03:51.315609     SYSTEM        DEAL_CARDS                NaN   
2024-11-21_15:03:51.327717  RANDOM_01           DISCARD          C11;Q4;J0   
2024-11-21_15:03:51.336602  RANDOM_02           DISCARD               pass   
...                               ...               ...                ...   
2024-11-21_15:06:08.055500  RANDOM_01           DISCARD               pass   
2024-11-21_15:06:08.067496  RANDOM_02           DISCARD           C8;Q1;J0   
2024-11-21_15:06:08.070494  RANDOM_02     DECLARE_PIZZA                NaN   
2024-11-21_15:06:08.341109     SYSTEM         END_MATCH                NaN   
2024-11-21_15:06:08.345109     SYSTEM    END_EXPERIMENT                NaN   

                           Player_Finished  \
2024-11-21_15:03:51.314611             NaN   
2024-11-21_15:03:51.314611             NaN   
2024-11-21_15:03:51.315609             NaN   
2024-11-21_15:03:51.327717             0.0   
2024-11-21_15:03:51.336602           False   
...                                    ...   
2024-11-21_15:06:08.055500           False   
2024-11-21_15:06:08.067496            True   
2024-11-21_15:06:08.070494             NaN   
2024-11-21_15:06:08.341109             NaN   
2024-11-21_15:06:08.345109             NaN   

                                                                 Player_Hands  \
2024-11-21_15:03:51.314611                                                NaN   
2024-11-21_15:03:51.314611                                                NaN   
2024-11-21_15:03:51.315609  [[3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 0, 0, 0,...   
2024-11-21_15:03:51.327717  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
...                                                                       ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2024-11-21_15:06:08.070494                                                NaN   
2024-11-21_15:06:08.341109                                                NaN   
2024-11-21_15:06:08.345109                                                NaN   

                                                     Board_Before  \
2024-11-21_15:03:51.314611                            

In [5]:
players = data['Agent_Names'][0]
players

C:\Users\alfio\AppData\Local\Temp\ipykernel_19524\3392628886.py:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  players = data['Agent_Names'][0]


['RANDOM_01', 'RANDOM_02', 'RANDOM_03', 'RANDOM_04']

In [6]:
data.columns

Index(['Match', 'Round', 'Agent_Names', 'Source', 'Action_Type',
       'Action_Description', 'Player_Finished', 'Player_Hands', 'Board_Before',
       'Board_After', 'Possible_Actions', 'Current_Roles', 'Match_Score',
       'Game_Score', 'Game_Performance_Score'],
      dtype='object')

In [7]:
data_refactored = data[(data['Match'] > 0) & (data['Round'] > 0) & (data['Action_Type'] == 'DISCARD')][['Match', 'Action_Description', 'Player_Hands', 'Board_Before', 'Possible_Actions']]

data_refactored



Match Action_Description  \
2024-11-21_15:03:51.327717      1          C11;Q4;J0   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1          C10;Q4;J0   
2024-11-21_15:03:51.365671      1           C9;Q4;J0   
...                           ...                ...   
2024-11-21_15:06:08.018273    100               pass   
2024-11-21_15:06:08.028495    100               pass   
2024-11-21_15:06:08.036495    100          C10;Q1;J0   
2024-11-21_15:06:08.055500    100               pass   
2024-11-21_15:06:08.067496    100           C8;Q1;J0   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  [2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  [0, 0, 0, 0, 2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10...   
2024-11-21_15:03:51.365671  [0, 0, 0, 0, 0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, ...   
...                                                                       ...   
2024-11-21_15:06:08.018273  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.028495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.036495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.336602  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.346670  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.356687  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.365671  [10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0]   
...                                                           ...   
2024-11-21_15:06:08.018273      [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.028495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.036495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.055500     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.067496     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:08.018273                                             [pass]  
2024-11-21_15:06:08.028495                                   [C8;Q1;J0, pass]  
2024-11-21_15:06:08.036495                       [C10;Q1;J0, C11;Q1;J0, pass]  
2024-11-21_15:06:08.055500                                  [C11;Q1;J0, pass]  
2024-11-21_15:06:08.067496                                   [C8;Q1;J0, pass]  

[9844 rows x 5 columns]

In data_refactored, Player_Hands lists the cards that remain in hand AFTER the player has taken the action described in Action_Description.
 
We want to restore the correct player hand so that the Possible_actions column refers to the current player hand and board.

In [8]:
Action_Description_Refactored = data[(data['Match'] > 0) & (data['Round'] > 0) & (data['Action_Type'] == 'DISCARD')]['Action_Description']

New_Action_Description = []

for i in Action_Description_Refactored:
    if i != 'pass':
        actionlist = i.split(';')
    else:
        actionlist = i
    New_Action_Description.append(actionlist)

data_refactored['Action_Description'] = New_Action_Description


In [9]:
Player_Hand_Refactored = []

for i in range(len(data_refactored)):
        newel = list(data_refactored['Player_Hands'][i])
        if data_refactored['Action_Description'][i] != 'pass':
                number = int(data_refactored['Action_Description'][i][0][1:])
                quantity = int(data_refactored['Action_Description'][i][1][1:])
                jolly = int(data_refactored['Action_Description'][i][2][1:])
                for k in range(quantity):
                        newel[newel.index(0)] = number
                for j in range(jolly):
                        newel[newel.index(0)] = 12
        newel.sort(reverse = False)
        newel = [int(i) for i in newel]
        Player_Hand_Refactored.append(newel)

data_refactored['Player_Hands'] = Player_Hand_Refactored
data_refactored

C:\Users\alfio\AppData\Local\Temp\ipykernel_19524\666179860.py:4: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  newel = list(data_refactored['Player_Hands'][i])
C:\Users\alfio\AppData\Local\Temp\ipykernel_19524\666179860.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if data_refactored['Action_Description'][i] != 'pass':
C:\Users\alfio\AppData\Local\Temp\ipykernel_19524\666179860.py:6: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:08.018273    100               pass   
2024-11-21_15:06:08.028495    100               pass   
2024-11-21_15:06:08.036495    100      [C10, Q1, J0]   
2024-11-21_15:06:08.055500    100               pass   
2024-11-21_15:06:08.067496    100       [C8, Q1, J0]   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  [3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  [2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  [2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:08.018273  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.028495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.036495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.336602  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.346670  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.356687  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.365671  [10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0]   
...                                                           ...   
2024-11-21_15:06:08.018273      [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.028495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.036495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.055500     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.067496     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:08.018273                                             [pass]  
2024-11-21_15:06:08.028495                                   [C8;Q1;J0, pass]  
2024-11-21_15:06:08.036495                       [C10;Q1;J0, C11;Q1;J0, pass]  
2024-11-21_15:06:08.055500                                  [C11;Q1;J0, pass]  
2024-11-21_15:06:08.067496                                   [C8;Q1;J0, pass]  

[9844 rows x 5 columns]

We now select only the unique pairs of (player_hand, board_state):

In [10]:
data_refactored['Player_Hands'] = data_refactored['Player_Hands'].apply(tuple)
data_refactored['Board_Before'] = data_refactored['Board_Before'].apply(tuple)

data_refactored_unique = data_refactored.drop_duplicates(subset = ['Player_Hands', 'Board_Before'])
data_refactored_unique

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:07.788984    100               pass   
2024-11-21_15:06:07.856173    100               pass   
2024-11-21_15:06:07.891175    100      [C11, Q1, J0]   
2024-11-21_15:06:07.904180    100      [C11, Q2, J0]   
2024-11-21_15:06:07.942268    100      [C10, Q3, J0]   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  (3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  (1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  (2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  (2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  (0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:07.788984  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:07.856173  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.891175  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.904180  (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10,...   
2024-11-21_15:06:07.942268  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.336602  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.346670  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.356687  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.365671  (10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0)   
...                                                           ...   
2024-11-21_15:06:07.788984     (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.856173      (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.891175     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.904180     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.942268     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:07.788984                         [C7;Q1;J0, C7;Q2;J0, pass]  
2024-11-21_15:06:07.856173                                             [pass]  
2024-11-21_15:06:07.891175  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.904180  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.942268  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  

[7819 rows x 5 columns]

In [11]:
balanced_df_train = data_refactored_unique[(data_refactored_unique['Match'] <= 97)]
balanced_df_train_shuffled = balanced_df_train.sample(frac=1, random_state = random_state).reset_index(drop=True) #The other random_states in the .sample() methods shall be left fixed in order to guarantee that the test set remains the same
balanced_df_train_shuffled

Match Action_Description  \
0        38       [C3, Q1, J0]   
1        11       [C8, Q3, J0]   
2        80               pass   
3         5      [C11, Q2, J0]   
4        10       [C4, Q1, J0]   
...     ...                ...   
7593     11               pass   
7594     65               pass   
7595     49       [C1, Q1, J0]   
7596      3               pass   
7597     64       [C6, Q2, J0]   

                                           Player_Hands  \
0     (0, 0, 0, 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 10...   
1     (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 8, 8, ...   
2     (0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 10, 10, 10, 11,...   
3     (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 11, 11...   
4     (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 6, 8, 10,...   
...                                                 ...   
7593  (0, 0, 4, 6, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 1...   
7594  (0, 2, 6, 6, 6, 6, 8, 8, 9, 10, 10, 10, 10, 10...   
7595  (0, 0, 0, 0, 0, 0, 0, 0, 1, 3, 5, 6, 9, 10, 11...   
7596  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10,...   
7597  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, ...   

                            Board_Before  \
0     (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
1      (9, 9, 9, 0, 0, 0, 0, 0, 0, 0, 0)   
2      (9, 9, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
3     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
4      (5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
...                                  ...   
7593  (12, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
7594   (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
7595  (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
7596  (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
7597  (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   

                                       Possible_Actions  
0     [C1;Q1;J0, C2;Q1;J0, C3;Q1;J0, C4;Q1;J0, C5;Q1...  
1                            [C8;Q3;J0, C8;Q4;J0, pass]  
2                                                [pass]  
3     [C5;Q1;J0, C9;Q1;J0, C11;Q1;J0, C11;Q2;J0, C11...  
4                                      [C4;Q1;J0, pass]  
...                                                 ...  
7593                                             [pass]  
7594                                   [C2;Q1;J0, pass]  
7595  [C1;Q1;J0, C3;Q1;J0, C5;Q1;J0, C6;Q1;J0, C9;Q1...  
7596                                             [pass]  
7597               [C5;Q1;J0, C6;Q1;J0, C6;Q2;J0, pass]  

[7598 rows x 5 columns]

In [12]:
balanced_df_test = data_refactored_unique[(data_refactored_unique['Match'] > 97)]
balanced_df_test_shuffled = balanced_df_test.sample(frac=1, random_state = 42).reset_index(drop=True)
balanced_df_test_shuffled

Match Action_Description  \
0       99               pass   
1       99               pass   
2       99               pass   
3      100       [C9, Q3, J0]   
4       98       [C8, Q1, J0]   
..     ...                ...   
216     99               pass   
217     98       [C9, Q1, J0]   
218     99       [C3, Q1, J0]   
219    100               pass   
220     99       [C7, Q1, J0]   

                                          Player_Hands  \
0    (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1    (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10...   
2    (5, 5, 5, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, ...   
3    (0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 8, 8, 9, 9, 9, ...   
4    (0, 0, 3, 3, 4, 4, 4, 6, 6, 7, 7, 8, 9, 9, 10,...   
..                                                 ...   
216  (0, 0, 0, 0, 0, 6, 7, 8, 8, 9, 9, 9, 10, 10, 1...   
217  (0, 0, 0, 0, 0, 0, 0, 0, 5, 5, 5, 6, 6, 9, 9, ...   
218  (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 1...   
219  (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 1...   
220  (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 1...   

                            Board_Before  \
0      (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
1    (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2      (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
3     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
4      (9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
..                                   ...   
216    (4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
217   (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
218   (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
219    (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
220   (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   

                                      Possible_Actions  
0                                               [pass]  
1                         [C10;Q2;J0, C10;Q3;J0, pass]  
2                                               [pass]  
3    [C6;Q1;J0, C8;Q1;J0, C8;Q2;J0, C9;Q1;J0, C9;Q2...  
4    [C3;Q1;J0, C3;Q2;J0, C4;Q1;J0, C4;Q2;J0, C4;Q3...  
..                                                 ...  
216                                             [pass]  
217  [C5;Q1;J0, C5;Q2;J0, C5;Q3;J0, C6;Q1;J0, C6;Q2...  
218  [C1;Q1;J0, C3;Q1;J0, C4;Q1;J0, C7;Q1;J0, C9;Q1...  
219                                             [pass]  
220  [C6;Q1;J0, C7;Q1;J0, C7;Q2;J0, C8;Q1;J0, C8;Q2...  

[221 rows x 5 columns]

# Experiments

We perform experiments with the Llama-3.1-8B-Instruct model from Huggingface. We adopt 4-bit quantization for improving speed and performances. In all of the experiments we include three settings.

In the first case we do not provide any explanation about the semantics of the input and just ask the model to complete the query based on the provided examples.

In the second case we provide a basic explanation of the input, without references to the rules of the game.

Last, we give a full explanation about the semantics of the input, the rules of the game, and include known techniques of prompt engineering.

We evaluate results according to several metrics: all_moves_accuracy (the fraction of instances for which the full correct list of legal moves is returned), TP (the number of correctly identified legal moves), FP (the number of illegal moves returned), FN (the legal moves which are not returned by the model) and IoU_lists (a variant of Intersection over Union for lists)

In [13]:
model_id = "meta-llama/Meta-Llama-3.1-8B-Instruct"

pipeline = transformers.pipeline(
    "text-generation",
    model=model_id,
    model_kwargs={"torch_dtype": torch.bfloat16,
                  "quantization_config": {"load_in_4bit": True}},
    device_map="cuda:0"
)

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda:0


## Experiment 2: KNN examples

In this second experiment, for each test instance, we retrieve the k closest examples in the "training" set according to the Hamming distance. Other similar (and more appropriate where the inputs are less structured) approaches could use distances or similarities between sentence embeddings.  

### No explanations provided

#### 5 examples

In [14]:
#### 5 EXAMPLES, NO DESCRIPTION OF THE TASK

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(5):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(5, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': 'Complete the following text. Only add the text that comes after "B:"'},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 0
IoU: 1.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']


['C10;Q2;J0', 'pass']
[np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('pass')] 

TP: 2
FN: 1
FP: 0
IoU: 0.6666666666666666 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 7, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0',

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['C3;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q1;J0', 'C10;Q1;J0', 'C11;Q1;J0', 'C11;Q1;J0']
[np.str_('pass')] 

TP: 0
FN: 1
FP: 5
IoU: 0.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: (0, 0, 0, 0, 5, 7, 7, 8, 8, 9, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C10;Q1;J0', 'C11;Q1

#### 10 examples

In [15]:
##### 10 EXAMPLES, NO DESCRIPTION OF THE TASK

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(10):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(10, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    #print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': 'Complete the following text. Only add the text that comes after "B:"'},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C9;Q1;J0', 'C11;Q1;J0', 'pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 2
IoU: 0.3333333333333333 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']
[np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('pass')] 

TP: 3
FN: 0
FP: 1
IoU: 0.75 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C1;Q1;J0', 'C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']
[np.str_('C1;Q1;J0'), np.str_('C3;Q1;J0'), np.str_('C4;Q1;J0'), np.str_('C7;Q1;J0'), np.str_('C9;Q1;J0'), np.str_('C9;Q2;J0'), np.str_('C10;Q1;J0'), np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('C10;Q4;J0'), np.str_('C11;Q1;J0'), np.str_('pass')] 

TP: 12
FN: 0
FP: 0
IoU: 1.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C3;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 8
IoU: 0.1111111111111111 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']
[np.str_('C6;Q1;J0'), np.str_('C7;Q1;J0'), np.str_('C7;Q2;J0'), np.str_('C8;Q1;J0'), np.str_('C8;Q2;J0'), np.str_('C9;Q1;J0'), np.str_('C9;Q2;J0'), np.str_('C9;Q3;J0'), np.str_('C10;Q1;J0'), np.str_('C10;Q2;J0'), np.str_('C11;Q1;J0'), np.str_('C11;Q2;J0'), np.str_('C11;Q3;J0'), np.str_('pass')] 

TP: 14
FN: 0
FP: 6
IoU: 0.7 


all_moves_accuracy: 0.167420814479638
Avg. IoU: 0.45114333247635774
TP total: 871
FP total: 1128
FN total: 90


#### 15 examples

In [16]:
# NO DESCRIPTION OF THE TASK AND RULES.

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(15):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(15, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    #print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': 'Complete the following text. Only add the text that comes after "B:"'},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C9;Q1;J0', 'pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 1
IoU: 0.5 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C10;Q3;J0', 'C10;Q4;J0', 'pass']
[np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('pass')] 

TP: 2
FN: 1
FP: 1
IoU: 0.5 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C1;Q1;J0', 'C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']
[np.str_('C1;Q1;J0'), np.str_('C3;Q1;J0'), np.str_('C4;Q1;J0'), np.str_('C7;Q1;J0'), np.str_('C9;Q1;J0'), np.str_('C9;Q2;J0'), np.str_('C10;Q1;J0'), np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('C10;Q4;J0'), np.str_('C11;Q1;J0'), np.str_('pass')] 

TP: 12
FN: 0
FP: 0
IoU: 1.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C3;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 9
IoU: 0.1 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']
[np.str_('C6;Q1;J0'), np.str_('C7;Q1;J0'), np.str_('C7;Q2;J0'), np.str_('C8;Q1;J0'), np.str_('C8;Q2;J0'), np.str_('C9;Q1;J0'), np.str_('C9;Q2;J0'), np.str_('C9;Q3;J0'), np.str_('C10;Q1;J0'), np.str_('C10;Q2;J0'), np.str_('C11;Q1;J0'), np.str_('C11;Q2;J0'), np.str_('C11;Q3;J0'), np.str_('pass')] 

TP: 14
FN: 0
FP: 6
IoU: 0.7 


all_moves_accuracy: 0.18552036199095023
Avg. IoU: 0.4603555022317408
TP total: 889
FP total: 1218
FN total: 72


### Minimal Description

#### 5 examples

In [17]:
#### 5 EXAMPLES, MINIMAL DESCRIPTION OF INPUT

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(5):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(5, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''In the following examples "A" provides two lists. The first list is a description of the cards in hand of a bord game player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card. Then, "B" replies with the full list of the current legal moves according to the description of "A". Complete the text by listing the correct legal moves given the last description from "A". Only add the text that comes after "B:"
'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['pass']
[np.str_('pass')] 

TP: 1
FN: 0
FP: 0
IoU: 1.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']


['C10;Q2;J0', 'pass']
[np.str_('C10;Q2;J0'), np.str_('C10;Q3;J0'), np.str_('pass')] 

TP: 2
FN: 1
FP: 0
IoU: 0.6666666666666666 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 7, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0',

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['C3;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0']
[np.str_('pass')] 

TP: 0
FN: 1
FP: 9
IoU: 0.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: (0, 0, 0, 0, 5, 7, 7, 8, 8, 9, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C10;Q1;J0', 'C11;Q1

#### 10 EXAMPLES

In [18]:
#### 10 EXAMPLES, MINIMAL DESCRIPTION OF INPUT

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(10):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(10, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''In the following examples "A" provides two lists. The first list is a description of the cards in hand of a bord game player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card. Then, "B" replies with the full list of the current legal moves according to the description of "A". Complete the text by listing the correct legal moves given the last description from "A". Only add the text that comes after "B:"
'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 3, 4, 4, 7, 8, 9, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C4;Q2;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0',

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 10, 10, 10, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 8, 9, 10, 10, 10, 11, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 7, 8, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C11;Q1;J0'

#### 15 Examples

In [19]:
#### 5 EXAMPLES, MINIMAL DESCRIPTION OF INPUT

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(15):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(15, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''In the following examples "A" provides two lists. The first list is a description of the cards in hand of a bord game player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card. Then, "B" replies with the full list of the current legal moves according to the description of "A". Complete the text by listing the correct legal moves given the last description from "A". Only add the text that comes after "B:"
'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 10), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 9), (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 9, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 10, 10, 10, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 8, 9, 10, 10, 10, 11, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 7, 8, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: (0, 0, 0, 6, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 

### Full description

#### 5 Examples

In [20]:
#### 5 EXAMPLES, FULL DESCRIPTION OF INPUT AND RULES

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(5):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(5, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''You are an expert board game player, and you are playing a new card game called Chef\'s Hat. In the following examples "A" provides two lists. The first list is a description of the cards in hand of a player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card, while a "12" represents a Joker card. "B" replies with the full list of the current legal moves according to the description of "A". The move 'CX;QY;JZ' means that Y cards with value X are played, while JZ indicates that Z Jokers are played.\n
                 As a player, you must play cards on top of all the cards that have been placed on the board before. The cards played must all have the same value, and this value must be strictly lower than the value of cards currently on the board. You cannot place less cards on the board than the amount of cards currently present there. If you have Joker cards, you can use them as if they had any value.\n
Complete the text by listing all the current legal moves given the last description from "A". Only add the text that comes after "B:"'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['C8;Q1;J0', 'C7;Q1;J0', 'C6;Q1;J0', 'C5;Q1;J0', 'C4;Q1;J0', 'C3;Q1;J0', 'C2;Q1;J0', 'C1;Q1;J0', 'C0;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C9;Q5;J0', 'C9;Q6;J0', 'C9;Q7;J0', 'C9;Q8;J0', 'C9;Q9;J0', 'C9;Q10;J0', 'C9;Q11;J0', 'C9;Q12;J0', 'C9;Q13;J1']
[np.str_('pass')] 

TP: 0
FN: 1
FP: 21
IoU: 0.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']


['C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C9;Q5;J0', 'C9;Q6;J0', 'C9;Q7;J0', 'C9;Q8;J0', 'C9;Q9;J0', 'C9;Q10;J0', 'C9;Q11;J0', 'C9;Q12;J0', 'C9;Q13;J0', 'C9;Q14;J0', 'C9;Q15;J0', 'C9;Q16;J0', 'C9;Q17;J0', 'C9

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 7, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 7, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0',

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']


['C0;Q1;J0', 'C2;Q1;J0', 'C1;Q1;J0']
[np.str_('pass')] 

TP: 0
FN: 1
FP: 3
IoU: 0.0 




Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: (0, 0, 0, 0, 5, 7, 7, 8, 8, 9, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C9;Q4;J0', 'C10;Q1;J0', 'C11;Q1

#### 10 Examples

In [21]:
#### 10 EXAMPLES, FULL DESCRIPTION OF INPUT AND RULES

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(10):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(10, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''You are an expert board game player, and you are playing a new card game called Chef\'s Hat. In the following examples "A" provides two lists. The first list is a description of the cards in hand of a player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card, while a "12" represents a Joker card. "B" replies with the full list of the current legal moves according to the description of "A". The move 'CX;QY;JZ' means that Y cards with value X are played, while JZ indicates that Z Jokers are played.\n
                 As a player, you must play cards on top of all the cards that have been placed on the board before. The cards played must all have the same value, and this value must be strictly lower than the value of cards currently on the board. You cannot place less cards on the board than the amount of cards currently present there. If you have Joker cards, you can use them as if they had any value.\n
Complete the text by listing all the current legal moves given the last description from "A". Only add the text that comes after "B:"'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 3, 4, 4, 7, 8, 9, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C4;Q2;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0',

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 10, 10, 10, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 8, 9, 10, 10, 10, 11, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 7, 8, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C8;Q3;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C11;Q1;J0'

#### 15 Examples

In [22]:
#### 15 EXAMPLES, FULL DESCRIPTION OF INPUT AND RULES

count = 0
IoU = 0
TP = 0
FN = 0
FP = 0

for i in range(len(balanced_df_test_shuffled)):

    query = 'A: '+ str(balanced_df_test_shuffled.iloc[i]['Player_Hands'])+', '+str(balanced_df_test_shuffled.iloc[i]['Board_Before'])+'\n'+'B: '

    ##Here we retrieve the examples with minimal hamming distance
    examples = {}

    for j in range(15):
        # Convert lists to tuples so they can be used as dictionary keys
        key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
               tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
            tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
    
        # Hamming distance calculation
        train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
        test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
    
        examples[key] = hamming(train_data, test_data)


    max_hamming = max(examples.values())


    for j in range(15, len(balanced_df_train_shuffled)):
        temp_hamming = hamming(balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before'], balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before'])
        if temp_hamming < max_hamming:
            del examples[max(examples, key=lambda k: examples[k])]
            key = (tuple(balanced_df_train_shuffled.iloc[j]['Player_Hands']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Board_Before']), 
                    tuple(balanced_df_train_shuffled.iloc[j]['Possible_Actions']))
            train_data = balanced_df_train_shuffled.iloc[j]['Player_Hands'] + balanced_df_train_shuffled.iloc[j]['Board_Before']
            test_data = balanced_df_test_shuffled.iloc[i]['Player_Hands'] + balanced_df_test_shuffled.iloc[i]['Board_Before']
            examples[key] = hamming(train_data, test_data)
            max_hamming = max(examples.values())
    

    text_examples = ''
    for j in list(examples):
        text_examples += 'A: '+ str(j[0])+', '+str(j[1])+'\n'
        text_examples += 'B: '+ str(str([str(el) for el in j[2]]))+'\n\n'
    print('query:', query)
    print('retrieved examples:', text_examples)

    messages = [{'role': 'system', 'content': '''You are an expert board game player, and you are playing a new card game called Chef\'s Hat. In the following examples "A" provides two lists. The first list is a description of the cards in hand of a player. The second list is a description of the cards that are already on the board. In both cases a "0" represents a missing card, while a "12" represents a Joker card. "B" replies with the full list of the current legal moves according to the description of "A". The move 'CX;QY;JZ' means that Y cards with value X are played, while JZ indicates that Z Jokers are played.\n
                 As a player, you must play cards on top of all the cards that have been placed on the board before. The cards played must all have the same value, and this value must be strictly lower than the value of cards currently on the board. You cannot place less cards on the board than the amount of cards currently present there. If you have Joker cards, you can use them as if they had any value.\n
Complete the text by listing all the current legal moves given the last description from "A". Only add the text that comes after "B:"'''},{"role": "user", "content": text_examples},{"role": "user", "content": query}]
    
    outputs = pipeline(
        messages,
        #max_length=1053,
        max_new_tokens=500
    )
    ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
    final_output = [elem[1:-1] for elem in ref_output]
    print(final_output)
    print(balanced_df_test_shuffled.iloc[i]['Possible_Actions'],'\n')

    if final_output == balanced_df_test_shuffled.iloc[i]['Possible_Actions']:
        count += 1

    TP_temp = len(set(final_output) & set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    TP += TP_temp
    print('TP:', TP_temp)

    FN_temp = len(set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']) - set(final_output))
    FN += FN_temp
    print('FN:', FN_temp)

    FP_temp = len(set(final_output) - set(balanced_df_test_shuffled.iloc[i]['Possible_Actions']))
    FP += FP_temp
    print('FP:', FP_temp)

    IoU_serv = IoU_lists(final_output, balanced_df_test_shuffled.iloc[i]['Possible_Actions'])
    IoU += IoU_serv
    print('IoU:', IoU_serv,'\n\n')
    
print('all_moves_accuracy:', count/len(balanced_df_test_shuffled))
print('Avg. IoU:', IoU/len(balanced_df_test_shuffled))
print('TP total:', TP)
print('FP total:', FP)
print('FN total:', FN)


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11), (9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 10), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 9), (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 9, 11), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10), (11, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11), (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 6, 9, 10, 10, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 11, 11), (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query: A: (0, 0, 0, 0, 0, 0, 1, 3, 4, 7, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 9, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 3, 4, 6, 8, 8, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 6, 6, 8, 8, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C6;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 9, 10, 10, 10, 10, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 8, 9, 10, 10, 10, 11, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 6, 9, 10, 10, 10, 10, 11), (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 11, 11), (1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 6, 9, 10, 10, 10, 11, 11), (5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 7, 8, 10, 10, 10, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query: A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: 
retrieved examples: A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C7;Q3;J0', 'pass']

A: (0, 0, 0, 0, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10, 11, 11, 11), (2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: (0, 0, 0, 0, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C7;Q2;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'pass']

A: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11), (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: (0, 0, 0, 6, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10, 10, 11), (7, 0, 0, 0, 0, 0, 0, 0, 0, 